<a href="https://www.kaggle.com/code/sabinakhadysy/spaceship-titanic-competition?scriptVersionId=147556604" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
#Imports
import numpy as np
import pandas as pd
from ydata_profiling import ProfileReport

from sklearn.model_selection import train_test_split,cross_val_score,StratifiedKFold
from sklearn.metrics import accuracy_score
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.metrics import mean_absolute_error
from sklearn.linear_model import LogisticRegression
from xgboost import XGBRegressor

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
/opt/conda/lib/python3.10/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
/opt/conda/lib/python3.10/site-packages/visions/backends/shared/nan_handling.py:51: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-o

# Loading data

In [2]:
#Loading data
train_data = pd.read_csv("/kaggle/input/spaceship-titanic/train.csv", index_col = 'PassengerId') #data used to build the model
display(train_data.head())
test_data = pd.read_csv("/kaggle/input/spaceship-titanic/test.csv", index_col = 'PassengerId') #data used to create submission
display(test_data.head())

#Setting the target
y = train_data.Transported
#Setting all features
X = train_data.drop(columns = "Transported")

HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
PassengerId                                                         
0001_01         Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
0002_01          Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
0003_01         Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
0003_02         Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
0004_01          Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

             RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  \
PassengerId                                                         
0001_01              0.0        0.0           0.0     0.0     0.0   
0002_01            109.0        9.0          25.0   549.0    44.0   
0003_01             43.0     3576.0           0.0  6715.0    49.0   
0003_02              0.0     1283.0         371.0  3329.0   193.0   
0004_01            303.0       70.0         151.0   565.0     2.0   

                          Name  Transported  
PassengerId                                  
0001_01        Maham Ofracculy        False  
0002_01           Juanna Vines         True  
0003_01          Altark Susent        False  
0003_02           Solam Susent        False  
0004_01      Willy Santantines         True

HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
PassengerId                                                         
0013_01          Earth      True  G/3/S  TRAPPIST-1e  27.0  False   
0018_01          Earth     False  F/4/S  TRAPPIST-1e  19.0  False   
0019_01         Europa      True  C/0/S  55 Cancri e  31.0  False   
0021_01         Europa     False  C/1/S  TRAPPIST-1e  38.0  False   
0023_01          Earth     False  F/5/S  TRAPPIST-1e  20.0  False   

             RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  \
PassengerId                                                         
0013_01              0.0        0.0           0.0     0.0     0.0   
0018_01              0.0        9.0           0.0  2823.0     0.0   
0019_01              0.0        0.0           0.0     0.0     0.0   
0021_01              0.0     6652.0           0.0   181.0   585.0   
0023_01             10.0        0.0         635.0     0.0     0.0   

                         Name  
PassengerId                    
0013_01       Nelly Carsoning  
0018_01        Lerome Peckers  
0019_01       Sabih Unhearfus  
0021_01      Meratz Caltilter  
0023_01       Brence Harperez

In [3]:
#Getting overall information about train data
train_data_profile = ProfileReport(train_data, title = "Train dataset quick EDA")
train_data_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
#Getting overall information about tets data
test_data_profile = ProfileReport(test_data, title = "Test dataset quick EDA")
test_data_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Initial model using XGBRegressor

In [5]:
#Choosing initial features and setting initial X
features_in = ['HomePlanet', 'CryoSleep', 'Destination', 'Age', 'VIP']
X_in = X[features_in]
X_in.head()

HomePlanet CryoSleep  Destination   Age    VIP
PassengerId                                               
0001_01         Europa     False  TRAPPIST-1e  39.0  False
0002_01          Earth     False  TRAPPIST-1e  24.0  False
0003_01         Europa     False  TRAPPIST-1e  58.0   True
0003_02         Europa     False  TRAPPIST-1e  33.0  False
0004_01          Earth     False  TRAPPIST-1e  16.0  False

In [6]:
#Splitting data into training and test set
#first parameters
#train_X_in, val_X_in, train_y, val_y = train_test_split(X_in, y, random_state = 0)
#changed parameters
train_X_in, val_X_in, train_y, val_y = train_test_split(X_in, y, train_size = 0.8, test_size = 0.2, random_state = 0)

In [7]:
#Looking for missing values
print(f'Shape of training data is {train_X_in.shape}')

missing_val_count_by_col = train_X_in.isnull().sum()
print(f'Columns with sum of missing values:\n {missing_val_count_by_col}')


Shape of training data is (6954, 5)
Columns with sum of missing values:
 HomePlanet     156
CryoSleep      170
Destination    149
Age            146
VIP            176
dtype: int64


In [8]:
#preprocessing for numerical data
numerical_col = ["Age"]
numerical_transformer = SimpleImputer(strategy = "median")

#preporcessing for categorical data
categorical_col = ["HomePlanet", "CryoSleep", "Destination", "VIP"]
categorical_transformer = OneHotEncoder(handle_unknown = "ignore")

#Bundle preprocesisng
preprocessor = ColumnTransformer(
    transformers =[
        ('num', numerical_transformer, numerical_col),
        ('cat', categorical_transformer, categorical_col)
    ]
)

#Buildign the model
initial_model = XGBRegressor()

# Bundle preprocessing and modeling code in a pipeline
pipeline = Pipeline(steps=[('preprocessor', preprocessor),
                           ('model', initial_model)
                          ])

#Preprocessing of training data and fitting the model
pipeline.fit(train_X_in, train_y)

#Preprocessing of validation data and getting predictions
preds = pipeline.predict(val_X_in)

print(f'MAE: {mean_absolute_error(preds, val_y)}')

MAE: 0.36213088035583496


In [9]:
#Checking parameters of initial model
initial_model

XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=None, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=None, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             n_estimators=100, n_jobs=None, num_parallel_tree=None,
             predictor=None, random_state=None, ...)

In [10]:
#Changing parameters in XGBRegressor()
initial_model_p1 = XGBRegressor(objective="binary:logistic", random_state = 42, n_estimators = 1000)
#Training the model
pipeline_p1 = Pipeline(steps=[('preprocessor', preprocessor),
                              ('model', initial_model_p1)
                             ])
pipeline_p1.fit(train_X_in, train_y)
preds_p1 = pipeline_p1.predict(val_X_in)

print(f'MAE p1: {mean_absolute_error(preds_p1, val_y)}')

MAE p1: 0.35789528489112854


# Adding feature engineering

In [11]:
#Calcualting the total amount spend on luxuries by each passenger
X1= X.copy()
X1["LuxTotalPass"] = X1.RoomService + X1.FoodCourt + X1.ShoppingMall + X1.Spa + X1.VRDeck
X1.head()

HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
PassengerId                                                         
0001_01         Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
0002_01          Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
0003_01         Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
0003_02         Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
0004_01          Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

             RoomService  FoodCourt  ShoppingMall     Spa  VRDeck  \
PassengerId                                                         
0001_01              0.0        0.0           0.0     0.0     0.0   
0002_01            109.0        9.0          25.0   549.0    44.0   
0003_01             43.0     3576.0           0.0  6715.0    49.0   
0003_02              0.0     1283.0         371.0  3329.0   193.0   
0004_01            303.0       70.0         151.0   565.0     2.0   

                          Name  LuxTotalPass  
PassengerId                                   
0001_01        Maham Ofracculy           0.0  
0002_01           Juanna Vines         736.0  
0003_01          Altark Susent       10383.0  
0003_02           Solam Susent        5176.0  
0004_01      Willy Santantines        1091.0

In [12]:
#Choosing features and setting X
features_FE = ['HomePlanet', 'CryoSleep', 'Destination', 'Age', 'VIP', 'LuxTotalPass']
X_FE = X1[features_FE]
X_FE.head()

HomePlanet CryoSleep  Destination   Age    VIP  LuxTotalPass
PassengerId                                                             
0001_01         Europa     False  TRAPPIST-1e  39.0  False           0.0
0002_01          Earth     False  TRAPPIST-1e  24.0  False         736.0
0003_01         Europa     False  TRAPPIST-1e  58.0   True       10383.0
0003_02         Europa     False  TRAPPIST-1e  33.0  False        5176.0
0004_01          Earth     False  TRAPPIST-1e  16.0  False        1091.0

In [13]:
#Splitting data into training and test set
train_X_FE, val_X_FE, train_y_FE, val_y_FE = train_test_split(X_FE, y, train_size = 0.8, test_size = 0.2, random_state = 0)

#Looking for missing values
print(f'Shape of training data is {train_X_FE.shape}')

missing_val_count_by_col_FE = train_X_FE.isnull().sum()
print(f'Columns with sum of missing values:\n {missing_val_count_by_col_FE}')

Shape of training data is (6954, 6)
Columns with sum of missing values:
 HomePlanet      156
CryoSleep       170
Destination     149
Age             146
VIP             176
LuxTotalPass    743
dtype: int64


In [14]:
#preprocessing for numerical data
numerical_col_FE = ["Age", "LuxTotalPass"]
numerical_transformer_FE = SimpleImputer(strategy = "median")

#preporcessing for categorical data
categorical_col_FE = ["HomePlanet", "CryoSleep", "Destination", "VIP"]
categorical_transformer_FE = OneHotEncoder(handle_unknown = "ignore")

#Bundle preprocesisng
preprocessor_FE = ColumnTransformer(
    transformers =[
        ('num', numerical_transformer_FE, numerical_col_FE),
        ('cat', categorical_transformer_FE, categorical_col_FE)
    ]
)

#Buildign the model
model_FE = XGBRegressor(objective="binary:logistic",random_state = 42, n_estimators = 1500)

# Bundle preprocessing and modeling code in a pipeline
pipeline_FE = Pipeline(steps=[('preprocessor', preprocessor_FE),
                           ('model', model_FE)
                          ])

#Preprocessing of training data and fitting the model
pipeline_FE.fit(train_X_FE, train_y_FE)

#Preprocessing of validation data and getting predictions
preds_FE = pipeline_FE.predict(val_X_FE)

print(f'MAE_FE: {mean_absolute_error(preds_FE, val_y_FE)}')

MAE_FE: 0.3381296992301941


# Logistic regression model with cross validation

In [15]:
features_LR = ['HomePlanet', 'CryoSleep', 'Destination', 'Age', 'VIP']
X_LR = X[features_LR]
X_LR.head()

HomePlanet CryoSleep  Destination   Age    VIP
PassengerId                                               
0001_01         Europa     False  TRAPPIST-1e  39.0  False
0002_01          Earth     False  TRAPPIST-1e  24.0  False
0003_01         Europa     False  TRAPPIST-1e  58.0   True
0003_02         Europa     False  TRAPPIST-1e  33.0  False
0004_01          Earth     False  TRAPPIST-1e  16.0  False

In [16]:
#Creating a pipeline

#preprocessing for numerical data
numerical_col_LR = ["Age"]
numerical_transformer_LR = SimpleImputer(strategy = "median")

#preporcessing for categorical data
categorical_col_LR = ["HomePlanet", "CryoSleep", "Destination", "VIP"]
categorical_transformer_LR = OneHotEncoder(handle_unknown = "ignore")


#Bundle preprocesisng
preprocessor_LR = ColumnTransformer(
    transformers =[
        ('num', numerical_transformer_LR, numerical_col_LR),
        ('cat', categorical_transformer_LR, categorical_col_LR)
    ]
)

#Building the model
model_LR = LogisticRegression()

# Bundle preprocessing and modeling code in a pipeline
pipeline_LR = Pipeline(steps=[('preprocessor', preprocessor_LR),
                           ('model', model_LR)
                          ])

# Create a stratified k-fold cross-validator
skf_LR = StratifiedKFold(n_splits=3, shuffle=True, random_state=100)

#Iterating through the folds, fitting and evaluating the model
for train_index, test_index in skf_LR.split(X, y):
    train_X_LR, val_X_LR = X_LR.iloc[train_index], X_LR.iloc[test_index]
    train_y_LR, val_y_LR = y.iloc[train_index], y.iloc[test_index]

    pipeline_LR.fit(train_X_LR, train_y_LR)
    preds_LR = pipeline_LR.predict(val_X_LR)

    accuracy = accuracy_score(val_y_LR, preds_LR)
    print("Fold accuracy:", accuracy)

/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Fold accuracy: 0.7056590752242926
Fold accuracy: 0.7301587301587301
Fold accuracy: 0.7117707973765964


# Logistic regression model with cross validation and feature engineering

In [17]:
#Choosing features and setting X
features_LRFE = ['HomePlanet', 'CryoSleep', 'Destination', 'Age', 'VIP', 'LuxTotalPass']
X_LRFE = X1[features_LRFE]
X_LRFE.head()

HomePlanet CryoSleep  Destination   Age    VIP  LuxTotalPass
PassengerId                                                             
0001_01         Europa     False  TRAPPIST-1e  39.0  False           0.0
0002_01          Earth     False  TRAPPIST-1e  24.0  False         736.0
0003_01         Europa     False  TRAPPIST-1e  58.0   True       10383.0
0003_02         Europa     False  TRAPPIST-1e  33.0  False        5176.0
0004_01          Earth     False  TRAPPIST-1e  16.0  False        1091.0

In [18]:
#Creating a pipeline

#preprocessing for numerical data
numerical_col_LRFE = ["Age", "LuxTotalPass"]
numerical_transformer_LRFE = SimpleImputer(strategy = "median")

#preporcessing for categorical data
categorical_col_LRFE = ["HomePlanet", "CryoSleep", "Destination", "VIP"]
categorical_transformer_LRFE = OneHotEncoder(handle_unknown = "ignore")


#Bundle preprocesisng
preprocessor_LRFE = ColumnTransformer(
    transformers =[
        ('num', numerical_transformer_LRFE, numerical_col_LRFE),
        ('cat', categorical_transformer_LRFE, categorical_col_LRFE)
    ]
)

#Building the model
model_LRFE = LogisticRegression()

# Bundle preprocessing and modeling code in a pipeline
pipeline_LRFE = Pipeline(steps=[('preprocessor', preprocessor_LRFE),
                           ('model', model_LRFE)
                          ])

# Create a stratified k-fold cross-validator
skf_LRFE = StratifiedKFold(n_splits=3, shuffle=True, random_state=100)

#Iterating through the folds, fitting and evaluating the model
for train_index, test_index in skf_LRFE.split(X, y):
    train_X_LRFE, val_X_LRFE = X_LRFE.iloc[train_index], X_LRFE.iloc[test_index]
    train_y_LRFE, val_y_LRFE = y.iloc[train_index], y.iloc[test_index]

    pipeline_LRFE.fit(train_X_LRFE, train_y_LRFE)
    preds_LRFE = pipeline_LRFE.predict(val_X_LRFE)

    accuracy = accuracy_score(val_y_LRFE, preds_LRFE)
    print("Fold accuracy:", accuracy)

Fold accuracy: 0.709799861973775
Fold accuracy: 0.7270531400966184


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Fold accuracy: 0.720745598895409


# Generating a submission

In [19]:
#Creating test_X containing columns with features from test dataset

#initial model
#test_X = test_data[features_in] 

#model with feature engineering
# test_data_FE = test_data.copy()
# test_data_FE["LuxTotalPass"] = test_data_FE.RoomService + test_data_FE.FoodCourt + test_data_FE.ShoppingMall + test_data_FE.Spa + test_data_FE.VRDeck
# display(test_data_FE.head())
# test_X_FE = test_data_FE[features_FE]
# display(test_X_FE.head())

#model with linear regression
# test_data_LR = test_data.copy()
# test_X_LR =  test_data_LR[features_LR]

#model with linear regression and feature engineering
test_data_LRFE = test_data.copy()
test_data_LRFE["LuxTotalPass"] = test_data_LRFE.RoomService + test_data_LRFE.FoodCourt + test_data_LRFE.ShoppingMall + test_data_LRFE.Spa + test_data_LRFE.VRDeck
#display(test_data_LRFE.head())
test_X_LRFE = test_data_LRFE[features_FE]
#display(test_X_LRFE.head())

#Making predicitions
#test_pred = pipeline.predict(test_X) #initial model
#test_pred_FE = pipeline_FE.predict(test_X_FE) #model with feature engineering
# test_pred_LR = pipeline_LR.predict(test_X_LR) #model with linear regression
test_pred_LRFE = pipeline_LRFE.predict(test_X_LRFE) #model with linear regression and feature engineering


In [20]:
#Changing numerical values of test_pred into True and False
threshold = 0.5
#binary_labels = ["True" if p >= threshold else "False" for p in test_pred] #initial model
#binary_labels_FE = ["True" if p >= threshold else "False" for p in test_pred_FE] #model with feature engineering
#binary_labels_LR = ["True" if p >= threshold else "False" for p in test_pred_LR] #model with linear regression
binary_labels_LRFE = ["True" if p >= threshold else "False" for p in test_pred_LRFE] #model with linear regression and feature engineering
print(binary_labels_LRFE[0:3])

['True', 'False', 'True']


In [21]:
#Generating a submission; for each submission one have to change name of binary_labels_...
output = pd.DataFrame({'Transported': binary_labels_LRFE}, index = test_data.index)
output.to_csv('my_submission.csv')
print("Your submission was successfully saved!")

Your submission was successfully saved!


In [22]:
output

Transported
PassengerId            
0013_01            True
0018_01           False
0019_01            True
0021_01           False
0023_01           False
...                 ...
9266_02            True
9269_01           False
9271_01            True
9273_01            True
9277_01            True

[4277 rows x 1 columns]